In [29]:
import time

import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

import IPython.display as ipd

from scipy.io import wavfile as wav

from sklearn import preprocessing
from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score, precision_score, recall_score, confusion_matrix
import tensorflow as tf
from tensorflow.keras import regularizers
import tensorflow.keras as keras
from tensorflow.keras import Sequential
from tensorflow.keras.layers import *
from tensorflow.keras.regularizers import l2
from tensorflow.keras.callbacks import ReduceLROnPlateau,EarlyStopping,ModelCheckpoint,LearningRateScheduler, Callback

from tqdm import tqdm
import plotly.graph_objects as go

colors = [
    '#1f77b4',  # muted blue
    '#ff7f0e',  # safety orange
    '#2ca02c',  # cooked asparagus green
    '#d62728',  # brick red
    '#9467bd',  # muted purple
    '#8c564b',  # chestnut brown
    '#e377c2',  # raspberry yogurt pink
    '#7f7f7f',  # middle gray
    '#bcbd22',  # curry yellow-green
    '#17becf'   # blue-teal
]



In [28]:
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())


[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 16897529384223470261
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 16149905408
locality {
  bus_id: 1
  links {
  }
}
incarnation: 2601446602643911835
physical_device_desc: "device: 0, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:04.0, compute capability: 6.0"
]


2022-11-16 19:50:36.953348: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-16 19:50:36.953929: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-16 19:50:36.954287: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-16 19:50:36.954745: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-16 19:50:36.955118: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from S

In [3]:
def Alice(plaintext_length, drop = 0., fc_layers = 1, activation = "sigmoid"):
    N = plaintext_length
    plaintext_in = Input((N, ), name = "plaintext_input")
    key_in = Input((N, ), name = "key_input")
    x = concatenate([plaintext_in, key_in])
    for i in range(fc_layers):
        x = Dense(2 * N, activation = activation)(x)
        x = Dropout(drop)(x)
    x = tf.expand_dims(x, -1)
    x = Conv1D(2, 4, strides = 1, padding = "same", activation = activation)(x)
    x = Conv1D(4, 2, strides = 2, padding = "same", activation = activation)(x)
    x = Conv1D(4, 1, strides = 1, padding = "same", activation = activation)(x)
    x = Conv1D(1, 1, strides = 1, padding = "same", activation = "tanh")(x)
    outputs = tf.squeeze(x, axis = -1)
    model = keras.Model(inputs = [plaintext_in, key_in], outputs = outputs)
    return model

def Bob(ciphertext_length, drop = 0., fc_layers = 1, activation = "sigmoid"):
    N = ciphertext_length
    ciphertext_in = Input((N, ), name = "ciphertext_input")
    key_in = Input((N, ), name = "key_input")
    x = concatenate([ciphertext_in, key_in])
    for i in range(fc_layers):
        x = Dense(2 * N, activation = activation)(x)
        x = Dropout(drop)(x)
    x = tf.expand_dims(x, -1)
    x = Conv1D(2, 4, strides = 1, padding = "same", activation = activation)(x)
    x = Conv1D(4, 2, strides = 2, padding = "same", activation = activation)(x)
    x = Conv1D(4, 1, strides = 1, padding = "same", activation = activation)(x)
    x = Conv1D(1, 1, strides = 1, padding = "same", activation = "tanh")(x)
    outputs = tf.squeeze(x, axis = -1)
    model = keras.Model(inputs = [ciphertext_in, key_in], outputs = outputs)
    return model

def Eve(plaintext_length, drop = 0., fc_layers = 1, activation = "sigmoid"):
    N = plaintext_length
    ciphertext_in = Input((N, ), name = "ciphertext_input")
    
    x = ciphertext_in
    for i in range(fc_layers):
        x = Dense(2 * N, activation = activation)(x)
        x = Dropout(drop)(x)
    x = tf.expand_dims(x, axis = -1)
    x = Conv1D(2, 4, strides = 1, padding = "same", activation = activation)(x)
    x = Conv1D(4, 2, strides = 2, padding = "same", activation = activation)(x)
    x = Conv1D(4, 1, strides = 1, padding = "same", activation = activation)(x)
    x = Conv1D(1, 1, strides = 1, padding = "same", activation = "tanh")(x)
    outputs = tf.squeeze(x, axis = -1)
    model = keras.Model(inputs = ciphertext_in, outputs = outputs)
    return model


In [4]:
def get_random_batch(batch_size, string_length):
    return tf.cast(tf.random.uniform((batch_size, string_length), minval = 0, maxval = 2, dtype = "int32") * 2 - 1, "float32")
plaintext = get_random_batch(1, 64)
key =  get_random_batch(1, 64)
print(key)

2022-11-16 19:20:27.099670: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-16 19:20:27.100885: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-16 19:20:27.101845: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-16 19:20:27.103758: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-11-16 19:20:27.104645: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from S

tf.Tensor(
[[ 1.  1.  1.  1. -1.  1. -1.  1.  1.  1.  1. -1.  1.  1. -1.  1.  1. -1.
  -1. -1. -1.  1.  1. -1. -1.  1.  1.  1.  1.  1.  1.  1.  1. -1.  1. -1.
   1. -1. -1. -1.  1. -1. -1. -1.  1. -1.  1. -1. -1.  1.  1. -1.  1. -1.
  -1. -1.  1. -1. -1.  1. -1.  1.  1. -1.]], shape=(1, 64), dtype=float32)


In [5]:
alice = Alice(64)
alice([plaintext, key])

2022-11-16 19:20:29.084367: I tensorflow/stream_executor/cuda/cuda_dnn.cc:369] Loaded cuDNN version 8005


<tf.Tensor: shape=(1, 64), dtype=float32, numpy=
array([[-0.1163566 , -0.11894512, -0.12118492, -0.11807856, -0.12001783,
        -0.12020132, -0.1196587 , -0.117137  , -0.12090397, -0.12096772,
        -0.12033857, -0.11817371, -0.11913345, -0.11793803, -0.12099194,
        -0.11899586, -0.11819947, -0.11959344, -0.12109108, -0.11809361,
        -0.11743011, -0.11960372, -0.1200527 , -0.11863695, -0.11943534,
        -0.11777479, -0.11981528, -0.11994946, -0.1198608 , -0.11945802,
        -0.11977675, -0.12066587, -0.11854442, -0.11745206, -0.12035449,
        -0.11994255, -0.12002333, -0.12114723, -0.11890931, -0.11988827,
        -0.11950231, -0.11860415, -0.11842447, -0.12034149, -0.11891829,
        -0.12053815, -0.11903296, -0.1194295 , -0.11811633, -0.12040838,
        -0.11970375, -0.11704317, -0.12049925, -0.1189917 , -0.12146207,
        -0.11835986, -0.11962458, -0.12183209, -0.11837634, -0.12144104,
        -0.11786076, -0.11977436, -0.11925481, -0.11990344]],
      dtype=f

In [15]:
class L1(keras.losses.Loss):
    def __init__(self):
        super().__init__()
    def call(self, y, y_pred):
        return tf.reduce_mean(tf.reduce_sum(tf.abs(y - y_pred) / 2, axis = 1), axis = 0)
    def batch_loss(self, y, y_pred):
        return tf.reduce_sum(tf.abs(y - y_pred) / 2, axis = 1)
    
class AliceBobLoss(keras.losses.Loss):
    def __init__(self, N):
        super().__init__()
        self.N = N
    def update_eve_loss(self, eve_loss):
        self.eve_loss = eve_loss
    def call(self, y, y_bob):
        L1_comp = tf.reduce_mean(tf.reduce_sum(tf.abs(y - y_bob) / 2, axis = 1))
        eve_comp = tf.reduce_mean(tf.square(self.N / 2 - self.eve_loss)) / ((self.N /2) **2)
        return L1_comp + eve_comp
        
        
def mean_reconstruction_accuracy(y, y_pred):
    y_pred = tf.cast(y_pred > 0, "float32") * 2 - 1
    return tf.reduce_mean(1 - tf.abs(y - y_pred)/2).numpy()
    
def eve_train_loop(alice, eve, optimizer,
                  num_batches = 10000,
                batch_size = 4096,
                string_length = 64,
                verbose = False
                ):
    L1_loss = L1()
    alice_bob_loss =  AliceBobLoss(string_length)
    history = {
              "eve_recon_acc": [],
              "eve_loss":[],
              }
    for i in tqdm(range(num_batches)):
        with tf.GradientTape() as tape:
            P = get_random_batch(batch_size, string_length)
            K = get_random_batch(batch_size, string_length)

            C = alice([P, K])
            
            P_eve = eve(C)
            
            
            eve_recon_acc = mean_reconstruction_accuracy(P, P_eve)
            eve_loss = L1_loss(P, P_eve)

            grads = tape.gradient(eve_loss, eve.trainable_weights)
            optimizer.apply_gradients(zip(grads,eve.trainable_weights))
        history["eve_recon_acc"].append(eve_recon_acc)
        history["eve_loss"].append(eve_loss)
        if verbose and i % 200 == 0:
            
            print("Batch: ", str(i))
            print("Eve's reconstruction accuracy: {:.2f}%".format(eve_recon_acc * 100))
            print("Eve's loss: {:.2f}".format(eve_loss.numpy()))
        
    return history, eve
def retrain_eve(fc_layers = 1,
                drop = 0.,
                activation = "sigmoid",
                learning_rate = 0.0008,
                num_batches = 10000,
                batch_size = 4096,
                string_length = 64,
                verbose = False
                  ):
    
    optimizer = tf.keras.optimizers.Adam(learning_rate=learning_rate)
    
    alice = Alice(string_length,fc_layers = fc_layers, drop= drop, activation = activation)
    eve = Eve(string_length,fc_layers = fc_layers, drop= drop, activation = activation)
    return eve_train_loop(alice, eve, optimizer,
                  num_batches,
                batch_size ,
                string_length,
                verbose)
def train_loop(alice, bob, eve,
               optimizer,
                learning_rate = 0.0008,
                num_batches = 10000,
                alice_bob_batches = 1,
                eve_batches = 2,
                batch_size = 4096,
                string_length = 64,
                verbose = False
                ):
    alice_bob_batch_count = 0
    eve_batch_count = 0
    L1_loss = L1()
    alice_bob_loss =  AliceBobLoss(string_length)
    history = {"bob_recon_acc": [],
              "eve_recon_acc": [],
              "eve_loss":[],
              "ab_loss": []}
    for i in tqdm(range(num_batches)):
        with tf.GradientTape(persistent = True) as tape:
            P = get_random_batch(batch_size, string_length)
            K = get_random_batch(batch_size, string_length)

            C = alice([P, K])
            P_bob = bob([C, K])
            P_eve = eve(C)
            
            bob_recon_acc = mean_reconstruction_accuracy(P, P_bob)
            eve_recon_acc = mean_reconstruction_accuracy(P, P_eve)
            eve_loss = L1_loss(P, P_eve)
            alice_bob_loss.update_eve_loss(eve_loss)
            ab_loss = alice_bob_loss(P, P_bob)

            if alice_bob_batch_count < alice_bob_batches:

                alice_grads = tape.gradient(ab_loss, alice.trainable_weights)
                bob_grads = tape.gradient(ab_loss, bob.trainable_weights)
                optimizer.apply_gradients(zip(alice_grads, alice.trainable_weights))
                optimizer.apply_gradients(zip(bob_grads, bob.trainable_weights))
                alice_bob_batch_count += 1
                
            elif eve_batch_count < eve_batches:
                grads = tape.gradient(eve_loss, eve.trainable_weights)
                optimizer.apply_gradients(zip(grads,eve.trainable_weights))
                eve_batch_count +=1
                
            else:
                alice_bob_batch_count = 0
                eve_batch_count = 0
                alice_grads = tape.gradient(ab_loss, alice.trainable_weights)
                bob_grads = tape.gradient(ab_loss, bob.trainable_weights)
                
                optimizer.apply_gradients(zip(alice_grads, alice.trainable_weights))
                optimizer.apply_gradients(zip(bob_grads, bob.trainable_weights))
                alice_bob_batch_count += 1
        del tape
        history["bob_recon_acc"].append(bob_recon_acc)
        history["eve_recon_acc"].append(eve_recon_acc)
        history["eve_loss"].append(eve_loss)
        history["ab_loss"].append(ab_loss)
        if verbose and i % 200 == 0:
            
            print("Batch: ", str(i))
            print("Bob's reconstruction accuracy: {:.2f}%".format(bob_recon_acc * 100))
            print("Eve's reconstruction accuracy: {:.2f}%".format(eve_recon_acc * 100))
            print("Bob and Alice's loss: {:.2f}".format(ab_loss.numpy()))
            print("Eve's loss: {:.2f}".format(eve_loss.numpy()))
    
    return history, alice, bob, eve
    

In [16]:
def run_experiment(fc_layers = 1,
                drop = 0.,
                activation = "sigmoid",
                learning_rate = 0.0008,
                num_batches = 10000,
                alice_bob_batches = 1,
                eve_batches = 2,
                batch_size = 4096,
                string_length = 64,
                verbose = False
                  ):
    
    optimizer = tf.keras.optimizers.Adam(learning_rate=learning_rate)
    
    alice = Alice(string_length,fc_layers = fc_layers, drop= drop, activation = activation)
    bob = Bob(string_length,fc_layers = fc_layers, drop= drop, activation = activation)
    eve = Eve(string_length,fc_layers = fc_layers, drop= drop, activation = activation)
    
    return train_loop(alice, bob, eve,
               optimizer,
                learning_rate,
                num_batches,
                alice_bob_batches,
                eve_batches,
                batch_size,
                string_length,
                verbose
                )

In [17]:
base_models_history, base_alice, base_bob, base_eve  = run_experiment(num_batches = 15000, string_length = 16, verbose = True)

  0%|          | 5/15000 [00:00<10:08, 24.65it/s]

Batch:  0
Bob's reconstruction accuracy: 50.05%
Eve's reconstruction accuracy: 49.95%
Bob and Alice's loss: 7.99
Eve's loss: 8.00


  1%|▏         | 207/15000 [00:06<08:00, 30.82it/s]

Batch:  200
Bob's reconstruction accuracy: 49.75%
Eve's reconstruction accuracy: 50.25%
Bob and Alice's loss: 8.03
Eve's loss: 7.99


  3%|▎         | 406/15000 [00:14<08:15, 29.45it/s]

...

 97%|█████████▋| 14604/15000 [08:36<00:16, 23.40it/s]

Batch:  14600
Bob's reconstruction accuracy: 100.00%
Eve's reconstruction accuracy: 56.86%
Bob and Alice's loss: 0.03
Eve's loss: 6.91


 99%|█████████▊| 14807/15000 [08:43<00:06, 29.82it/s]

Batch:  14800
Bob's reconstruction accuracy: 100.00%
Eve's reconstruction accuracy: 56.74%
Bob and Alice's loss: 0.03
Eve's loss: 6.92


100%|██████████| 15000/15000 [08:50<00:00, 28.30it/s]


In [30]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = [*range(15000)], y = base_models_history["bob_recon_acc"],
    name = "Bob's reconstruction accuracy",
     mode="lines",
    line = dict(color = colors[0])
))

fig.add_trace(go.Scatter(
    x = [*range(15000)], y = base_models_history["eve_recon_acc"],
    name = "Eve's reconstruction accuracy",
     mode="lines",
    line = dict(color = colors[1])
))

fig.show()

In [33]:
base_retrained_eve = retrain_eve(num_batches = 15000, verbose = True)

  0%|          | 3/15000 [00:00<09:27, 26.43it/s]

Batch:  0
Eve's reconstruction accuracy: 50.02%
Eve's loss: 32.00


  1%|▏         | 204/15000 [00:08<09:57, 24.77it/s]

Batch:  200
Eve's reconstruction accuracy: 50.10%
Eve's loss: 31.98


  3%|▎         | 405/15000 [00:16<10:14, 23.74it/s]

...

 97%|█████████▋| 14605/15000 [09:49<00:15, 25.27it/s]

Batch:  14600
Eve's reconstruction accuracy: 68.94%
Eve's loss: 21.20


 99%|█████████▊| 14805/15000 [09:57<00:07, 25.15it/s]

Batch:  14800
Eve's reconstruction accuracy: 68.92%
Eve's loss: 21.15


100%|██████████| 15000/15000 [10:05<00:00, 24.78it/s]


In [34]:
base_retrained_eve_history, base_retrained_eve = base_retrained_eve

In [35]:
fig = go.Figure()

fig.add_trace(go.Scatter(
    x = [*range(15000)], y = base_retrained_eve_history["eve_recon_acc"],
    name = "Eve's reconstruction accuracy",
     mode="lines",
    line = dict(color = colors[1])
))

fig.show()

# Different string sizes

In [36]:
s32_hist, s32_alice, s32_bob, s32_eve = run_experiment(num_batches = 18000, string_length = 32)
s64_hist, s64_alice, s64_bob, s64_eve = run_experiment(num_batches = 18000, string_length = 64)


100%|██████████| 18000/18000 [19:19<00:00, 15.52it/s]


In [38]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = base_models_history["bob_recon_acc"],
    name = "length = 16",
     mode="lines",
    line = dict(color = colors[0])
))

fig.add_trace(go.Scatter(
    x = [*range(18000)], y = s32_hist["bob_recon_acc"],
    name = "length = 32",
     mode="lines",
    line = dict(color = colors[1])
))
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = s64_hist["bob_recon_acc"],
    name = "length = 64",
     mode="lines",
    line = dict(color = colors[2])
))
fig.update_layout(title="Bob's reconstruction error between different string length", showlegend = True)
fig.show()

In [39]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = base_models_history["eve_recon_acc"],
    name = "length = 16",
     mode="lines",
    line = dict(color = colors[0])
))

fig.add_trace(go.Scatter(
    x = [*range(18000)], y = s32_hist["eve_recon_acc"],
    name = "length = 32",
     mode="lines",
    line = dict(color = colors[1])
))
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = s64_hist["eve_recon_acc"],
    name = "length = 64",
     mode="lines",
    line = dict(color = colors[2])
))
fig.update_layout(title="Eve's reconstruction error between different string length", showlegend = True)
fig.show()

# Fully connected layers size

In [41]:
fc3_hist, fc3_alice, fc3_bob, fc3_eve = run_experiment(num_batches = 18000, string_length = 16, fc_layers = 3)
fc4_hist, fc4_alice, fc4_bob, fc4_eve = run_experiment(num_batches = 18000, string_length = 16, fc_layers = 4)


100%|██████████| 18000/18000 [13:08<00:00, 22.84it/s]


In [48]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = base_models_history["bob_recon_acc"],
    name = "fc layers = 1",
     mode="lines",
    line = dict(color = colors[0])
))

fig.add_trace(go.Scatter(
    x = [*range(18000)], y = fc3_hist["bob_recon_acc"],
    name = "fc layers = 3",
     mode="lines",
    line = dict(color = colors[1])
))
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = fc4_hist["bob_recon_acc"],
    name = "fc layers = 4",
     mode="lines",
    line = dict(color = colors[2])
))
fig.update_layout(title="Bob's reconstruction error between different number of FC layers", showlegend = True)
fig.show()

In [49]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = base_models_history["eve_recon_acc"],
    name = "fc layers = 1",
     mode="lines",
    line = dict(color = colors[0])
))

fig.add_trace(go.Scatter(
    x = [*range(18000)], y = fc3_hist["eve_recon_acc"],
    name = "fc layers = 3",
     mode="lines",
    line = dict(color = colors[1])
))
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = fc4_hist["eve_recon_acc"],
    name = "fc layers = 4",
     mode="lines",
    line = dict(color = colors[2])
))
fig.update_layout(title="Eve's reconstruction error between different number of FC layers", showlegend = True)
fig.show()

# Learning rate

In [51]:
lr00005_hist, lr00005_alice, lr00005_bob, lr00005_eve = run_experiment(num_batches = 18000, string_length = 16, learning_rate = 0.0005)
lr00012_hist, lr0002_alice, lr0002_bob, lr00012_eve = run_experiment(num_batches = 18000, string_length = 16, learning_rate = 0.0012)

100%|██████████| 18000/18000 [10:34<00:00, 28.38it/s]


In [53]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = base_models_history["bob_recon_acc"],
    name = "learning rate = 0.0008",
     mode="lines",
    line = dict(color = colors[0])
))

fig.add_trace(go.Scatter(
    x = [*range(18000)], y = lr00005_hist["bob_recon_acc"],
    name = "learning rate = 0.0005",
     mode="lines",
    line = dict(color = colors[1])
))
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = lr00012_hist["bob_recon_acc"],
    name = "learning rate = 0.0012",
     mode="lines",
    line = dict(color = colors[2])
))
fig.update_layout(title="Bob's reconstruction error between different learning rates", showlegend = True)
fig.show()

In [55]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = base_models_history["eve_recon_acc"],
    name = "learning rate = 0.0008",
     mode="lines",
    line = dict(color = colors[0])
))

fig.add_trace(go.Scatter(
    x = [*range(18000)], y = lr00005_hist["eve_recon_acc"],
    name = "learning rate = 0.0005",
     mode="lines",
    line = dict(color = colors[1])
))
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = lr00012_hist["eve_recon_acc"],
    name = "learning rate = 0.0012",
     mode="lines",
    line = dict(color = colors[2])
))
fig.update_layout(title="Eve's reconstruction error between different learning rates", showlegend = True)
fig.show()

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = base_models_history["eve_recon_acc"],
    name = "learning rate = 0.0008",
     mode="lines",
    line = dict(color = colors[0])
))

fig.add_trace(go.Scatter(
    x = [*range(18000)], y = lr00005_hist["eve_recon_acc"],
    name = "learning rate = 0.0005",
     mode="lines",
    line = dict(color = colors[1])
))
fig.add_trace(go.Scatter(
    x = [*range(18000)], y = lr00012_hist["eve_recon_acc"],
    name = "learning rate = 0.0012",
     mode="lines",
    line = dict(color = colors[2])
))
fig.update_layout(title="Eve's reconstruction error between different learning rates", showlegend = True)
fig.show()

# Save model

In [57]:
!mkdir models
base_alice.save("./models/alice")
base_bob.save("./models/bob")
base_eve.save("./models/eve")

2022-11-16 22:03:50.185951: W tensorflow/python/util/util.cc:348] Sets are not currently considered sequences, but this may change in the future, so consider avoiding using them.


In [58]:
!zip -r models.zip models

  adding: models/ (stored 0%)
  adding: models/bob/ (stored 0%)
  adding: models/bob/saved_model.pb (deflated 90%)
  adding: models/bob/variables/ (stored 0%)
  adding: models/bob/variables/variables.data-00000-of-00001 (deflated 38%)
  adding: models/bob/variables/variables.index (deflated 55%)
  adding: models/bob/assets/ (stored 0%)
  adding: models/bob/keras_metadata.pb (deflated 92%)
  adding: models/eve/ (stored 0%)
  adding: models/eve/saved_model.pb (deflated 90%)
  adding: models/eve/variables/ (stored 0%)
  adding: models/eve/variables/variables.data-00000-of-00001 (deflated 47%)
  adding: models/eve/variables/variables.index (deflated 55%)
  adding: models/eve/assets/ (stored 0%)
  adding: models/eve/keras_metadata.pb (deflated 92%)
  adding: models/alice/ (stored 0%)
  adding: models/alice/saved_model.pb (deflated 89%)
  adding: models/alice/variables/ (stored 0%)
  adding: models/alice/variables/variables.data-00000-of-00001 (deflated 37%)
  adding: models/alice/variables/

In [59]:
from IPython.display import FileLink

FileLink(r'./models.zip')

/kaggle/working/models.zip

# Live demo

In [64]:
alice = tf.keras.models.load_model('models/alice')
bob = tf.keras.models.load_model('models/bob')
eve = tf.keras.models.load_model('models/eve')

In [126]:
def test_string(string, key):
    bits = [int(i) for i in string]
    key_bits = [int(k) for k in key]
    P = tf.expand_dims(tf.convert_to_tensor(bits, dtype = "float32") * 2 - 1, axis = 0)
    K = tf.expand_dims(tf.convert_to_tensor(key_bits, dtype = "float32") * 2 - 1, axis = 0)
    
    C = alice([P, K], training = False)
    P_bob = bob([C, K], training = False)
    P_eve = eve(C, training = False)
    
    C_string = "".join([str(i) for i in ((tf.cast(tf.squeeze(C) > 0, "int32"))).numpy().tolist()])
    P_bob_string = "".join([str(i) for i in ((tf.cast(tf.squeeze(P_bob) > 0, "int32"))).numpy().tolist()])
    P_eve_string = "".join([str(i) for i in ((tf.cast(tf.squeeze(P_eve) > 0, "int32"))).numpy().tolist()])
    print("Plaintext: \t", string)
    print("Ciphertext: \t", C_string)
    print("Raw ciphertext: \t ", C.numpy())
    print("Bob's output:\t", P_bob_string)
    print("Eve's output:\t", P_eve_string)

In [134]:
test_string("0000000000000000", "0000000000000000")

Plaintext: 	 0000000000000000
Ciphertext: 	 1010000101000101
Raw ciphertext: 	  [[ 0.59209484 -0.47203982  0.5898849  -0.3578894  -0.64312327 -0.7108566
  -0.5153211   0.6126271  -0.40734392  0.7457158  -0.39334875 -0.5966818
  -0.10165622  0.7035398  -0.43351054  0.56441486]]
Bob's output:	 0000000000000000
Eve's output:	 0001010010001101


In [128]:
!pip install pycryptodome

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 2.1 MB/s eta 0:00:0000:0100:010m


In [139]:
!pip install bitarray

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.4/235.4 kB 460.5 kB/s eta 0:00:00a 0:00:01


In [222]:
from Crypto.Cipher import AES
from bitarray import bitarray


In [248]:
def test_readable_string(string, key = "0000000000000000"):
    start = time.perf_counter()
    ba = bitarray()
    ba.frombytes(string.encode("utf-8"))
    bits = [int(x) for x in ba.tolist()]
     
    key_bits = [int(k) for k in key]
    key_bits = [key_bits for i in range(int(len(bits) / 16))]
    bits = [bits[16*i:16*i+16] for i in range(int(len(bits) / 16))]
   
    
    P = tf.convert_to_tensor(bits, dtype = "float32") * 2 - 1,
    K = tf.convert_to_tensor(key_bits, dtype = "float32") * 2 - 1
    
    C = alice([P, K], training = False)
    P_bob = bob([C, K], training = False)
    P_eve = eve(C, training = False)

    P_bob_string = bitarray((tf.cast(tf.squeeze(P_bob) > 0, "int32")).numpy().flatten().tolist()).tobytes().decode("utf-8")
    print("Plaintext: \t", string)
    print("Bob's output:\t", P_bob_string)
    try:
        P_eve_string = bitarray((tf.cast(tf.squeeze(P_eve) > 0, "int32")).numpy().flatten().tolist()).tobytes().decode("utf-8")
        print("Eve's output:\t", P_eve_string)
    except: 
        print("Eve's output:\t", "".join(str(i) for i in (tf.cast(tf.squeeze(P_eve) > 0, "int32").numpy().flatten().tolist())))
    end = time.perf_counter()
 
    
    print("Execution time: ", end - start, "(seconds)")

In [249]:
test_readable_string("Hello world!")

Plaintext: 	 Hello world!
Bob's output:	 Hello world!
Eve's output:	 010111001000110101011100100011010101110010001101010101001000110101010100100011010101010010001101
Execution time:  0.01697968000007677 (seconds)
